In [161]:
import pandas as pd
import glob
import os
import numpy as np

### Data Prep

In [3]:
ticker = pd.read_csv("/Users/yiliwang/Documents/ACR Internship/csi_300_pool.csv", header=0)

In [8]:
# To obtain numeric part of tickers by removing "SZSE_" and "SHSE" in front of tickers
SZ_rem = [item.replace("SZSE_", "") for item in ticker['ticker']]
both_rem = [item.replace("SHSE_", "") for item in SZ_rem]

In [12]:
len(both_rem) # List of Ticker Names

300

In [5]:
ticker[ticker['ticker'] == 'SZSE_000001']

date       ticker
168  2017-07-05  SZSE_000001

In [10]:
stk_p = pd.read_csv("/Users/yiliwang/Documents/ACR Internship/data/000001.SZ.csv", header=0)
# use S_DQ_ADJCLOSE

In [44]:
# generate the list of file/dataframe name
file_name = os.listdir("/Users/yiliwang/Documents/ACR Internship/data/")

In [45]:
file_name_nocsv = [f[:-4] for f in file_name] # remove ".csv" extension
df_name_list = [i.replace(".", "_") for i in file_name_nocsv] # replace "." with "_"

In [ ]:
path =r'/Users/yiliwang/Documents/ACR Internship/data/' # use your path
allFiles = glob.glob(path + "/*.csv")
frame = pd.DataFrame()
list_ = []
for file_ in allFiles:
    df = pd.read_csv(file_,index_col=None, header=0)

In [49]:
for i in range(len(df_name_list)):
    df_name_list[i] = pd.read_csv(allFiles[i],index_col=None, header=0)

In [55]:
df_name_list

[     S_INFO_WINDCODE  TRADE_DT  S_DQ_OPEN  S_DQ_HIGH  S_DQ_LOW  S_DQ_CLOSE  \
 0          000001.SZ  20130104      16.32      16.45     15.92       15.99   
 1          000001.SZ  20130107      15.98      16.35     15.88       16.30   
 2          000001.SZ  20130108      16.30      16.37     15.86       16.00   
 3          000001.SZ  20130109      15.96      16.02     15.80       15.86   
 4          000001.SZ  20130110      15.86      16.10     15.79       15.87   
 5          000001.SZ  20130111      15.87      16.04     15.45       15.54   
 6          000001.SZ  20130114      15.49      17.09     15.49       17.09   
 7          000001.SZ  20130115      17.12      17.92     17.09       17.61   
 8          000001.SZ  20130116      17.61      17.91     17.22       17.82   
 9          000001.SZ  20130117      17.70      18.28     17.46       17.74   
 10         000001.SZ  20130118      17.87      18.42     17.60       18.33   
 11         000001.SZ  20130121      18.30      19.7

##### Return of Portfolio: assume purchase one share of each stock?

### ------ STEP 1: To get Median ME ------
ME: S_VAL_MV

In [56]:
AShareEODDerivativeIndicator = pd.read_csv("/Users/yiliwang/Documents/ACR Internship/Supplementary datasets/EODDerivativeIndicator.csv", header=0)

In [103]:
ME_20130630_list = AShareEODDerivativeIndicator[AShareEODDerivativeIndicator['TRADE_DT'] == 20130630]['S_VAL_MV'] # 267 stocks available at 20130630

In [104]:
ME_20130630_list.median() # median of ME 20130630: 1966671.2519999999

1966671.2519999999

### ------ STEP2: To get BE/ME ------
BE: 股东权益 AShareBalanceSheet-'TOT_SHRHLDR_EQY_INCL_MIN_INT'

In [76]:
AShareBalanceSheet = pd.read_csv("/Users/yiliwang/Documents/ACR Internship/Supplementary datasets/BalanceSheet.csv", header=0)

###### 2.1 BE:  book equity for the last fiscal year end in t-1, which is 20120930

In [124]:
BE_20120930_df  = AShareBalanceSheet[AShareBalanceSheet['REPORT_PERIOD']==20120930]

In [131]:
len(BE_20120930_df['S_INFO_WINDCODE'].unique()) # 274 companies

274

###### However, there are more than 274 BEs in BE_20120930_df, since the dataframe contains different types of statement(408006000母公司报表, 40801000合并报表 )
母公司资产负债表、母公司利润表、母公司现金流量表，加上母公司所有者权益变动表，展示的是上市公司本部的经营情况。
对应的合并报表，并不是一个真实存在的法律实体，它合并了上市公司本部经营及控制的子公司、孙子公司经营情况。合并时，会抵销这些母公司、子孙公司之间的投资、交易和债权债务。

We assume 合并报表 could provides shareholders more information, so we use 合并报表(denoted as T1).

In [135]:
BE_20120930_T1 = BE_20120930_df[BE_20120930_df['STATEMENT_TYPE'] == 408001000] # 20120930 合并报表 BE, len = 274

In [141]:
BE_20120930_T1 #['TOT_SHRHLDR_EQY_INCL_MIN_INT']

OBJECT_ID S_INFO_WINDCODE  WIND_CODE  \
207    {01FD0833-6B7F-41E7-833A-2E249705A525}       000157.SZ  000157.SZ   
246    {0257DFFB-4C3E-4E75-8121-E5C0C1D8F6BF}       600682.SH  600682.SH   
281    {02AD1932-827D-4B19-8745-0750D051976A}       600685.SH  600685.SH   
454    {04780F10-BFB0-4426-B04D-0E3784EB03CF}       600489.SH  600489.SH   
474    {04BF1B7B-4733-4871-B3FA-16A5DD15F1A7}       600036.SH  600036.SH   
482    {04E38978-95F2-4D55-861F-B477BBAFE5AA}       600415.SH  600415.SH   
556    {05BFD687-86BA-4169-962B-9FFD0E74AF2F}       600649.SH  600649.SH   
739    {07A789AF-FC02-483D-8F9E-EFB38A923399}       000100.SZ  000100.SZ   
755    {07E52F00-520A-4804-960A-CAA1305DAB80}       002602.SZ  002602.SZ   
918    {095E9C6B-6494-4634-B061-29CBA566C2C4}       601985.SH  601985.SH   
1392   {0D63AA6C-50D7-4A9C-A8D8-956E55785F44}       000686.SZ  000686.SZ   
1673   {1063C909-A7C1-4BE2-A998-F2C7225B9228}       000423.SZ  000423.SZ   
1727   {10FD0F8D-CEFB-4897-B867-9E126927B9A6}       600352.SH  600352.SH   
1779   {116B044D-A946-49AE-B7D7-8132F117C2F5}       002558.SZ  002558.SZ   
1821   {11BF19CF-3C99-495E-A0D4-5B0084D59CC1}       000538.SZ  000538.SZ   
1881   {12517BDD-4D02-427F-8445-0417E3E05EF7}       600816.SH  600816.SH   
2096   {14793EA6-7988-4380-92BF-6A87D7CC0FC5}       002508.SZ  002508.SZ   
2406   {1778BA13-BFC5-4598-9245-B8AA75BBE1C6}       000625.SZ  000625.SZ   
2528   {18882782-183B-4048-9D88-6FA28C0BE84D}       000938.SZ  000938.SZ   
2541   {18ABAB1D-4CF0-49F7-928C-55602F187E99}       600177.SH  600177.SH   
2567   {18DF1B7B-ED3C-4E64-B604-A257425BC387}       600795.SH  600795.SH   
2612   {195E921C-5DB1-4451-AC8B-859276DCCD30}       600221.SH  600221.SH   
2626   {197DB9DF-3F1D-4084-8426-680A8D47AFEC}       601601.SH  601601.SH   
2627   {1982EBC7-9DBD-4709-8E43-D833C803A5BE}       600061.SH  600061.SH   
2632   {1992A815-D34D-4956-BE41-D902731153D8}       601998.SH  601998.SH   
2653   {19C4C5BD-3EB0-45BB-A80A-5D9DE24C3082}       600895.SH  600895.SH   
2672   {19EA1496-41ED-4CAD-9E21-A6EF3361DE4B}       300017.SZ  300017.SZ   
2948   {1CF46D26-2441-46D8-974F-70C23C09319B}       002292.SZ  002292.SZ   
3358   {218B9601-8DED-4E90-A0BD-A366A6F43472}       000792.SZ  000792.SZ   
3434   {2250EE00-2CD3-4442-9E23-F636FAF66BDF}       002736.SZ  002736.SZ   
...                                       ...             ...        ...   
33516  {E604852D-5BD2-4CF0-A55E-9F7DC3B0498C}       600376.SH  600376.SH   
33522  {E609B3CD-F5AB-43F9-BDEF-E69F0B4730A4}       600436.SH  600436.SH   
33561  {E6920FFC-E76C-4BA2-BDAA-A1C6FE16BD11}       002424.SZ  002424.SZ   
33601  {E6F15D25-7AFA-4B2B-B5E4-31FD6947CDF5}       000876.SZ  000876.SZ   
33748  {E8B3D9B2-1CDE-475E-B59B-045AA816BBF6}       600383.SH  600383.SH   
33792  {E92A9D80-6533-4A7D-89F3-734A377D4F78}       000630.SZ  000630.SZ   
34090  {EA08064D-473C-40EE-81D9-AE93EC9582A2}       002252.SZ  002252.SZ   
34094  {EA134E22-7057-47E6-99BF-890FF3B932E5}       600074.SH  600074.SH   
34118  {EA66F597-F28B-4B5E-A720-CA1E15694571}       300124.SZ  300124.SZ   
34147  {EAA1C67F-10D9-4181-B561-02D3F05A5162}       600037.SH  600037.SH   
34193  {EB41A166-2DE4-490C-AC2B-51157BAA443F}       600031.SH  600031.SH   
34204  {EB6DB967-78F2-436F-9EAD-004B91066949}       601555.SH  601555.SH   
34352  {ED0D482A-BF65-4F79-AE59-2C3D8674B8C2}       000568.SZ  000568.SZ   
34439  {EDD17320-7ADE-4731-8857-6F5776625262}       601997.SH  601997.SH   
34695  {F04804EA-9DFD-4C8B-9ABA-E7727759CA2D}       600115.SH  600115.SH   
34731  {F0A00104-EB82-48E0-B152-2B545C0E10EE}       000858.SZ  000858.SZ   
34745  {F0BB6174-D9C8-429D-8DDD-00A01759E469}       000728.SZ  000728.SZ   
34941  {F2961514-F4E1-4AE4-BDCC-7628647ED867}       600015.SH  600015.SH   
35226  {F5D9A351-25C8-4276-93C3-05D01AF7A251}       002465.SZ  002465.SZ   
35512  {F8EFCF67-8610-467E-BD23-EB352496C9E4}       601006.SH  601006.SH   
35525  {F9183330-1EC5-4171-B8E5-E14621D2AD8C}       601018.SH  601018.SH   
35633  {

###### 2.2 ME:   ME for December of t-1, which is 20121231

In [144]:
ME_20121231_df = AShareEODDerivativeIndicator[AShareEODDerivativeIndicator['TRADE_DT'] == 20121231] # 267

In [145]:
ME_20121231_df

OBJECT_ID S_INFO_WINDCODE  TRADE_DT  \
1150786  {D21BAE3F-B93F-D951-E040-C80A10011AAC}       002465.SZ  20121231   
1150787  {D21BAE3F-B94F-D951-E040-C80A10011AAC}       601118.SH  20121231   
1150788  {D21BAE3F-B957-D951-E040-C80A10011AAC}       601633.SH  20121231   
1150789  {D21BAE3F-B964-D951-E040-C80A10011AAC}       600233.SH  20121231   
1150790  {D21BAE3F-B966-D951-E040-C80A10011AAC}       600795.SH  20121231   
1150791  {D21BAE3F-B967-D951-E040-C80A10011AAC}       601818.SH  20121231   
1150792  {D21BAE3F-B97E-D951-E040-C80A10011AAC}       603993.SH  20121231   
1150793  {D21BAE3F-B981-D951-E040-C80A10011AAC}       600827.SH  20121231   
1150794  {D21BAE3F-B982-D951-E040-C80A10011AAC}       600060.SH  20121231   
1150795  {D21BAE3F-B98D-D951-E040-C80A10011AAC}       600816.SH  20121231   
1150796  {D21BAE3F-B9A1-D951-E040-C80A10011AAC}       600111.SH  20121231   
1150797  {D21BAE3F-B9A4-D951-E040-C80A10011AAC}       000627.SZ  20121231   
1150798  {D21BAE3F-B9CA-D951-E040-C80A10011AAC}       600871.SH  20121231   
1150799  {D21BAE3F-B9D8-D951-E040-C80A10011AAC}       300027.SZ  20121231   
1150800  {D21BAE3F-B9E2-D951-E040-C80A10011AAC}       600489.SH  20121231   
1150801  {D21BAE3F-B9E4-D951-E040-C80A10011AAC}       600332.SH  20121231   
1150802  {D21BAE3F-B9EF-D951-E040-C80A10011AAC}       000725.SZ  20121231   
1150803  {D21BAE3F-B9F3-D951-E040-C80A10011AAC}       600606.SH  20121231   
1150804  {D21BAE3F-BA07-D951-E040-C80A10011AAC}       000540.SZ  20121231   
1150805  {D21BAE3F-BA0C-D951-E040-C80A10011AAC}       600804.SH  20121231   
1150806  {D21BAE3F-BA17-D951-E040-C80A10011AAC}       002142.SZ  20121231   
1150807  {D21BAE3F-BA24-D951-E040-C80A10011AAC}       000750.SZ  20121231   
1150808  {D21BAE3F-BA34-D951-E040-C80A10011AAC}       600068.SH  20121231   
1150809  {D21BAE3F-BA38-D951-E040-C80A10011AAC}       601877.SH  20121231   
1150810  {D21BAE3F-BA3A-D951-E040-C80A10011AAC}       600535.SH  20121231   
1150811  {D21BAE3F-BA41-D951-E040-C80A10011AAC}       000858.SZ  20121231   
1150812  {D21BAE3F-BA43-D951-E040-C80A10011AAC}       601186.SH  20121231   
1150813  {D21BAE3F-BA57-D951-E040-C80A10011AAC}       601888.SH  20121231   
1150814  {D21BAE3F-BA5F-D951-E040-C80A10011AAC}       002027.SZ  20121231   
1150815  {D21BAE3F-BA73-D951-E040-C80A10011AAC}       600893.SH  20121231   
...                                         ...             ...       ...   
1151023  {D21BAE3F-C23D-D951-E040-C80A10011AAC}       600031.SH  20121231   
1151024  {D21BAE3F-C246-D951-E040-C80A10011AAC}       000568.SZ  20121231   
1151025  {D21BAE3F-C247-D951-E040-C80A10011AAC}       600660.SH  20121231   
1151026  {D21BAE3F-C24A-D951-E040-C80A10011AAC}       600016.SH  20121231   
1151027  {D21BAE3F-C24C-D951-E040-C80A10011AAC}       600895.SH  20121231   
1151028  {D21BAE3F-C24F-D951-E040-C80A10011AAC}       000002.SZ  20121231   
1151029  {D21BAE3F-C253-D951-E040-C80A10011AAC}       000783.SZ  20121231   
1151030  {D21BAE3F-C255-D951-E040-C80A10011AAC}       600100.SH  20121231   
1151031  {D21BAE3F-C25C-D951-E040-C80A10011AAC}       600690.SH  20121231   
1151032  {D21BAE3F-C273-D951-E040-C80A10011AAC}       601872.SH  20121231   
1151033  {D21BAE3F-C27A-D951-E040-C80A10011AAC}       000686.SZ  20121231   
1151034  {D21BAE3F-C27B-D951-E040-C80A10011AAC}       300168.SZ  20121231   
1151035  {D21BAE3F-C284-D951-E040-C80A10011AAC}       600208.SH  20121231   
1151036  {D21BAE3F-C29A-D951-E040-C80A10011AAC}       601288.SH  20121231   
1151037  {D21BAE3F-C29F-D951-E040-C80A10011AAC}       600018.SH  20121231   
1151038  {D21BAE3F-C2A3-D951-E040-C80A10011AAC}       600522.SH  20121231   
1151039  {D21BAE3F-C2A7-D951-E040-C80A10011AAC}       000623.SZ  20121231   
1151040  {D21BAE3F-C2B4-D951-E040-C80A10011AAC}       600570.SH  20121231   
1151041  {D21BAE3F-C2C4-D951-E040-C80A10011AAC}       002352.SZ  20121231   
1151042  {D21BAE3F-C2CA-D951-E040-C80A10011AAC}       600297.SH  20121231   
1151043  {D21BAE3F-C2CC-D951-E040-

In [147]:
# merge two dataframes by windcode
BEME_ratio_df = ME_20121231_df.merge(BE_20120930_T1, left_on='S_INFO_WINDCODE', right_on='S_INFO_WINDCODE', how='inner')

In [151]:
len(BEME_ratio_df['S_INFO_WINDCODE'].unique()) # 267 companies available for BE/ME ratio

267

###### 2.3 BE/ME Ratio and two boundaries (30 percentile and 70 percentile of BE/ME)

In [159]:
BEME_ratio_list = BEME_ratio_df['TOT_SHRHLDR_EQY_INCL_MIN_INT']/BEME_ratio_df['S_VAL_MV'] # Dataframe of calculated BE/ME 

In [171]:
BEME_pct_70 = np.percentile(np.array(BEME_ratio_list), 70)
print BEME_pct_70

6450.81594666


In [172]:
BEME_pct_30 = np.percentile(np.array(BEME_ratio_list), 30) 
print BEME_pct_30

3116.26482846


### ------ STEP3: Dividing stocks into 6 portfolios ------